# Agrupación de Direcciones por Cercanía usando Clustering Jerárquico

Este notebook realiza una agrupación de direcciones a partir de sus coordenadas geográficas (Latitud, Longitud) utilizando el algoritmo de **Agglomerative Clustering**. El objetivo es distribuir las direcciones en grupos de proximidad geográfica, con un **máximo de 30 direcciones por grupo**.


In [ ]:
# Clusterización para agrupar direcciones por cercanía

import pandas as pd
from sklearn.cluster import AgglomerativeClustering
from sklearn.preprocessing import StandardScaler



In [7]:
# Cargar el archivo con las coordenadas obtenidas
data = pd.read_excel('output_file_with_coordinates.xlsx')



In [9]:
# Parámetros para agrupación
max_grupos = 60  # Usamos un número mayor de clusters inicialmente
max_direcciones_por_grupo = 30

# Escalar las coordenadas
scaler = StandardScaler()
coords_scaled = scaler.fit_transform(data[['Latitud', 'Longitud']])



In [10]:
# Aplicar Agglomerative Clustering para un número mayor de clusters
agglo = AgglomerativeClustering(n_clusters=max_grupos, metric='euclidean', linkage='ward')
data['Grupo_Temporal'] = agglo.fit_predict(coords_scaled)

# Ajustar los grupos para que cada uno tenga un máximo de 30 direcciones
final_grupos = []
grupo_id = 0

# Recorremos cada grupo temporal y dividimos si es necesario
for grupo in data['Grupo_Temporal'].unique():
    subgrupo = data[data['Grupo_Temporal'] == grupo]
    # Dividimos el subgrupo en porciones de máximo 30 direcciones
    for i in range(0, len(subgrupo), max_direcciones_por_grupo):
        subgrupo_segmento = subgrupo.iloc[i:i + max_direcciones_por_grupo].copy()
        subgrupo_segmento['Grupo_Final'] = grupo_id
        final_grupos.append(subgrupo_segmento)
        grupo_id += 1

# Concatenar los subgrupos y guardar el resultado
data_final = pd.concat(final_grupos)
data_final.to_excel('Geo_grouped_40_clusters_max30.xlsx', index=False)
print("Archivo agrupado en 40 grupos de proximidad con máximo 30 direcciones guardado como 'Geo_grouped_40_clusters_max30.xlsx'")

Archivo agrupado en 40 grupos de proximidad con máximo 30 direcciones guardado como 'Geo_grouped_40_clusters_max30.xlsx'


In [12]:
df=data_final

In [14]:
print(df.columns.tolist())


['ID', 'CIUDAD', 'DIRECCION', 'Latitud', 'Longitud', 'Grupo_Temporal', 'Grupo_Final']


In [21]:
# Calcular cantidad de direcciones por grupo
conteo = df['Grupo_Temporal'].value_counts()

# Obtener los grupos con al menos 3 direcciones
grupos_validos = conteo[conteo >= 3].index

# Filtrar el DataFrame para quedarte solo con esos grupos
df_filtrado = df[df['Grupo_Temporal'].isin(grupos_validos)].copy()


In [24]:
df_filtrado['Grupo_Temporal'].nunique()

37

In [22]:
import folium
import pandas as pd
import random
from folium.plugins import MarkerCluster

# Cargar archivo
df = df_filtrado

# Usar solo Grupo_Temporal
grupo_col = 'Grupo_Temporal'

# Crear un color aleatorio por grupo
grupos_unicos = df[grupo_col].unique()
colores = {grupo: f'#{random.randint(0, 0xFFFFFF):06x}' for grupo in grupos_unicos}

# Crear mapa centrado en Valledupar
m = folium.Map(location=[10.4631, -73.2532], zoom_start=13)

# Agregar marcadores con colores por grupo
for _, row in df.iterrows():
    color = colores[row[grupo_col]]
    folium.CircleMarker(
        location=[row['Latitud'], row['Longitud']],
        radius=5,
        popup=f"Grupo: {row[grupo_col]}<br>Dirección: {row['DIRECCION']}",
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7
    ).add_to(m)

# Mostrar el mapa
m


In [20]:
import folium
import pandas as pd
import random
from folium.plugins import MarkerCluster

# Cargar archivo
df = pd.read_excel('Geo_grouped_40_clusters_max30.xlsx')

# Usar solo Grupo_Temporal
grupo_col = 'Grupo_Final'

# Crear un color aleatorio por grupo
grupos_unicos = df[grupo_col].unique()
colores = {grupo: f'#{random.randint(0, 0xFFFFFF):06x}' for grupo in grupos_unicos}

# Crear mapa centrado en Valledupar
m = folium.Map(location=[10.4631, -73.2532], zoom_start=13)

# Agregar marcadores con colores por grupo
for _, row in df.iterrows():
    color = colores[row[grupo_col]]
    folium.CircleMarker(
        location=[row['Latitud'], row['Longitud']],
        radius=5,
        popup=f"Grupo: {row[grupo_col]}<br>Dirección: {row['DIRECCION']}",
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7
    ).add_to(m)

# Mostrar el mapa
m

In [27]:
from sklearn.cluster import AgglomerativeClustering
from sklearn.preprocessing import StandardScaler
import pandas as pd
import numpy as np

# Centro de Valledupar para ordenar
centro_valledupar = [10.4631, -73.2532]

# Leer tus datos
# Cargar el archivo con las coordenadas obtenidas
data = pd.read_excel('output_file_with_coordinates.xlsx')

# Escalar coordenadas
coords = data[['Latitud', 'Longitud']]
scaler = StandardScaler()
coords_scaled = scaler.fit_transform(coords)

# Aplicar agrupamiento natural (sin limitar por tamaño)
agglo = AgglomerativeClustering(n_clusters=None, distance_threshold=0.01, linkage='ward')
data['Grupo_Temporal'] = agglo.fit_predict(coords_scaled)

# Ahora dividir los grupos > 30 direcciones, ordenando desde el centro de Valledupar
max_direcciones_por_grupo = 30
grupo_id = 0
grupos_finales = []

for grupo in data['Grupo_Temporal'].unique():
    subgrupo = data[data['Grupo_Temporal'] == grupo].copy()

    # Calcular distancia desde el centro de Valledupar
    subgrupo['DistanciaCentro'] = np.sqrt(
        (subgrupo['Latitud'] - centro_valledupar[0])**2 +
        (subgrupo['Longitud'] - centro_valledupar[1])**2
    )

    # Ordenar desde el más cercano al más lejano
    subgrupo = subgrupo.sort_values('DistanciaCentro')

    # Dividir en bloques de 30
    for i in range(0, len(subgrupo), max_direcciones_por_grupo):
        bloque = subgrupo.iloc[i:i + max_direcciones_por_grupo].copy()
        bloque['Grupo_Final'] = grupo_id
        grupos_finales.append(bloque)
        grupo_id += 1

# Concatenar y exportar
data_final = pd.concat(grupos_finales)
data_final.drop(columns='DistanciaCentro', inplace=True)
data_final.to_excel('Geo_grupos_divididos_por_distancia.xlsx', index=False)

print("✅ Agrupamiento ajustado guardado como 'Geo_grupos_divididos_por_distancia.xlsx'")


✅ Agrupamiento ajustado guardado como 'Geo_grupos_divididos_por_distancia.xlsx'


In [32]:
data_final['Grupo_Final'].value_counts()


Grupo_Final
2      30
7      30
3      30
4      30
5      30
       ..
131     1
133     1
134     1
135     1
136     1
Name: count, Length: 137, dtype: int64

In [44]:
# Calcular cantidad de direcciones por grupo
conteo = data_final['Grupo_Final'].value_counts()

# Obtener los grupos con al menos 3 direcciones
grupos_validos = conteo[conteo >= 15].index

# Filtrar el DataFrame para quedarte solo con esos grupos
df_filtrado = data_final[data_final['Grupo_Final'].isin(grupos_validos)].copy()

In [45]:
df_filtrado['Grupo_Final'].value_counts()

Grupo_Final
2      30
7      30
3      30
4      30
5      30
8      30
6      30
10     30
9      30
25     30
26     30
14     30
15     30
16     30
20     30
22     30
34     30
52     30
51     30
31     30
66     30
0      28
48     27
107    25
46     23
38     22
1      22
84     21
19     20
27     19
18     19
65     19
92     19
103    18
90     18
72     18
23     18
44     18
71     18
78     18
58     18
39     17
37     17
30     17
73     17
41     17
28     16
13     16
17     16
81     16
79     16
61     16
36     15
29     15
62     15
86     15
85     15
Name: count, dtype: int64

In [48]:
import folium
import pandas as pd
import random
from folium.plugins import MarkerCluster

# Cargar archivo
df = df_filtrado

# Usar solo Grupo_Temporal
grupo_col = 'Grupo_Final'

# Crear un color aleatorio por grupo
grupos_unicos = df[grupo_col].unique()
colores = {grupo: f'#{random.randint(0, 0xFFFFFF):06x}' for grupo in grupos_unicos}

# Crear mapa centrado en Valledupar
m = folium.Map(location=[10.4631, -73.2532], zoom_start=13)

# Agregar marcadores con colores por grupo
for _, row in df.iterrows():
    color = colores[row[grupo_col]]
    folium.CircleMarker(
        location=[row['Latitud'], row['Longitud']],
        radius=5,
        popup=f"Grupo: {row[grupo_col]}<br>Dirección: {row['DIRECCION']}",
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7
    ).add_to(m)

# Mostrar el mapa
m


In [50]:
import folium
import pandas as pd
import random
from folium.plugins import MarkerCluster

# Cargar el DataFrame ya filtrado
df = df_filtrado

# Seleccionar el grupo que quieres mostrar
grupo_objetivo = 41  # Cambia este número por el grupo que quieras visualizar

# Filtrar solo ese grupo
df_grupo = df[df['Grupo_Final'] == grupo_objetivo]

# Crear mapa centrado en Valledupar
m = folium.Map(location=[10.4631, -73.2532], zoom_start=13)

# Elegir un color para el grupo
color = f'#{random.randint(0, 0xFFFFFF):06x}'

# Agregar marcadores
for _, row in df_grupo.iterrows():
    folium.CircleMarker(
        location=[row['Latitud'], row['Longitud']],
        radius=5,
        popup=f"Grupo: {row['Grupo_Final']}<br>Dirección: {row['DIRECCION']}",
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7
    ).add_to(m)

# Mostrar el mapa
m
